In [8]:

gdf['City'].unique()
array(['Seattle', 'Washington DC Area', 'Houston', 'New York City',
       'Boston', 'Chicago', 'Jacksonville'], dtype=object)
merged_gdf['City_x'].unique()

array(['Seattle', 'Washington DC Area', 'Houston', 'New York City',
       'Boston', 'Chicago', 'Jacksonville', 'San Francisco Area',
       'Los Angeles', 'Phoenix'], dtype=object)

array(['Seattle', 'Washington DC Area', 'Houston', 'New York City',
       'Boston', 'Chicago', 'Jacksonville'], dtype=object)

In [9]:
import geopandas as gpd
import folium as fl
import pandas as pd

#updated date: Nov 19, 2024
#changes made: added city filter for map to scale, and made each census tract interactive. One note, between the gdf and merged_gdf, 'San Francisco Area','Los Angeles', 'Phoenix' are getting dropped. need to investigate why

# File paths
shapefile_path = "/Users/aishwaryaraj/Downloads/UrbanHealthCSE583/Updated_Shape_files/CT10_MetroAll.shp"
csv_path = "/Users/aishwaryaraj/Downloads/UrbanHealthCSE583/UpdateMetropolitanCensusTractsData.csv"

# Load the shapefile and CSV
gdf = gpd.read_file(shapefile_path)
csv_data = pd.read_csv(csv_path)

# Merge the GeoDataFrame with the CSV file
gdf['TRACTCE10'] = gdf['TRACTCE10'].astype(str)
csv_data['FGEOIDCT10'] = csv_data['FGEOIDCT10'].astype(str)

merged_gdf = gdf.merge(csv_data, left_on='GEOID10', right_on='FGEOIDCT10')
merged_gdf.columns

# Ask the user for a city name
city_name ='Washington DC Area'
## options are 


# Filter the GeoDataFrame for the selected city
# Replace 'city_name_column' with the column containing city names
if 'City_x' in merged_gdf.columns:
    city_gdf = merged_gdf[merged_gdf['City_x'].str.contains(city_name, case=False, na=False)]

    if city_gdf.empty:
        print(f"No data found for city: {city_name}. Please check the city name.")
    else:
        # Calculate the centroid and bounds of the selected city's region
        city_bounds = city_gdf.geometry.total_bounds  # [minx, miny, maxx, maxy]
        city_center = [
            city_gdf.geometry.centroid.y.mean(), 
            city_gdf.geometry.centroid.x.mean()
        ]

        # Create the folium map centered on the city
        m = fl.Map(location=city_center, zoom_start=12)

        # Add a choropleth layer for the city's census tracts
        fl.Choropleth(
            geo_data=city_gdf,
            data=city_gdf,
            columns=['TRACTCE10', 'Life Expectancy'],  # Columns for mapping
            key_on='feature.properties.TRACTCE10',
            fill_color='YlGnBu',
            fill_opacity=0.7,
            line_opacity=0.2,
            legend_name='Life Expectancy'
        ).add_to(m)

        # Add GeoJson with interactivity
        def style_function(feature):
            return {
                'fillColor': 'transparent',
                'color': 'black',
                'weight': 0.5,
                'fillOpacity': 0.5,
            }

        def highlight_function(feature):
            return {
                'fillColor': 'yellow',  # Color on hover
                'color': 'red',  # Border color on hover
                'weight': 2,  # Border weight on hover
                'fillOpacity': 0.7,
            }

        fl.GeoJson(
            city_gdf,
            style_function=style_function,
            highlight_function=highlight_function,
            tooltip=fl.GeoJsonTooltip(
                fields=['TRACTCE10', 'Life Expectancy'],  # Fields to display
                aliases=['Census Tract:', 'Life Expectancy(in age):'],  # Labels
                localize=True
            )
        ).add_to(m)

        # Add layer control and save the map
        fl.LayerControl().add_to(m)
        #m.save("city_input_map.html")
        
else:
    print("The GeoDataFrame does not contain a column for city names. Please check your data.")

m

/var/folders/nv/76pvm6h567s4931c7zyn_ckm0000gn/T/ipykernel_1593/2305855475.py:38: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  city_gdf.geometry.centroid.y.mean(),
/var/folders/nv/76pvm6h567s4931c7zyn_ckm0000gn/T/ipykernel_1593/2305855475.py:39: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  city_gdf.geometry.centroid.x.mean()
